In [7]:
from dask.distributed import Client

# Create a local cluster using all CPU cores
client = Client()

# Optional: See dashboard link for live task monitoring
print(client.dashboard_link)


/home/leochaussy/anaconda3/envs/dfg/lib/python3.11/site-packages/distributed/node.py:187: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 36743 instead
  warnings.warn(


http://127.0.0.1:36743/status


In [34]:
import dask.dataframe as dd

# Read large CSV file using Dask
df = dd.read_csv("./QUOT_SIM2_previous-2020-202507.csv", sep=";")

# Trigger a computation to make sure everything works
print(df.head())


   LAMBX  LAMBY      DATE  ...  WGI_RACINE_Q  TINF_H_Q  TSUP_H_Q
0    600  24010  20200101  ...           0.0       9.5      10.9
1    600  24010  20200102  ...           0.0       9.5      11.9
2    600  24010  20200103  ...           0.0       8.8      10.6
3    600  24010  20200104  ...           0.0       5.4      10.2
4    600  24010  20200105  ...           0.0       7.6       8.8

[5 rows x 28 columns]


In [36]:
#df.LAMBY.max().compute()
df.LAMBY.max().compute()

np.int64(26810)

In [20]:
pdf

LAMBX  LAMBY      DATE  TINF_H_Q  TSUP_H_Q
0         600  24010  20200101       9.5      10.9
1         600  24010  20200102       9.5      11.9
2         600  24010  20200103       8.8      10.6
3         600  24010  20200104       5.4      10.2
4         600  24010  20200105       7.6       8.8
...       ...    ...       ...       ...       ...
140719    600  24010  20250727      14.9      19.4
140720    600  24010  20250728      13.9      21.9
140721    600  24010  20250729      15.2      18.9
140722    600  24010  20250730      16.8      21.6
140723    600  24010  20250731      17.3      19.6

[2039 rows x 5 columns]

In [ ]:
import dask.dataframe as dd
import geopandas as gpd
from shapely.geometry import Point
import folium

# Step 1: Load data
df = dd.read_csv("./QUOT_SIM2_previous-2020-202507.csv", sep=";")

# Step 2: Filter for proximity to a given point
target_x, target_y, tolerance = 8793.3352, 20180.6811, 500
filtered_df = df[
    (df["LAMBX"].astype(float).between(target_x - tolerance, target_x + tolerance)) &
    (df["LAMBY"].astype(float).between(target_y - tolerance, target_y + tolerance))
][["LAMBX", "LAMBY", "DATE", "HTEURNEIGE_Q"]]

# Step 3: Compute to get a pandas DataFrame
pdf = filtered_df.compute()

# Step 4: Create GeoDataFrame in Lambert II étendu (EPSG:27572)
geometry = [Point(xy) for xy in zip(pdf["LAMBX"], pdf["LAMBY"])]
gdf = gpd.GeoDataFrame(pdf, geometry=geometry, crs="EPSG:27572")

# Step 5: Reproject to WGS84 (lat/lon) for folium
gdf = gdf.to_crs(epsg=4326)

# Step 6: Create interactive map centered at mean point
center = [gdf.geometry.y.mean(), gdf.geometry.x.mean()]
m = folium.Map(location=center, zoom_start=14)

# Step 7: Add points to map
for _, row in gdf.iterrows():
    folium.CircleMarker(
        location=(row.geometry.y, row.geometry.x),
        radius=5,
        #popup=f"Date: {row['DATE']}<br>TINF_H_Q: {row['TINF_H_Q']}<br>TSUP_H_Q: {row['TSUP_H_Q']}",
        color='blue',
        fill=True,
        fill_opacity=0.7,
    ).add_to(m)

# Step 8: Save or display map
m.save("interactive_map.html")

# If you run this in a Jupyter notebook, just do:
print("Map saved as interactive_map.html")
m


Map saved as interactive_map.html
